In [31]:
import os

import hashlib
import nacl.signing
from cryptography.hazmat.primitives.ciphers import Cipher, algorithms, modes
from cryptography.hazmat.backends import default_backend

In [7]:
sign_key = nacl.signing.SigningKey.generate()

In [44]:
make_action_string = lambda group, index: f'reset idx={index:08x} g={group}'.encode()
def generate_presig(group, index):
    action_string = make_action_string(group, index)
    sig = sign_key.sign(action_string)[:64] # cut off original message
    
    key = os.urandom(16)
    
    cipher = Cipher(algorithms.AES(key), modes.CTR(b'\0' * 16), backend=default_backend())
    enc = cipher.encryptor()
    ciphtertext = enc.update(sig)
    assert len(enc.finalize()) == 0
    
    return key, ciphtertext

presigs = { group: [ generate_presig(group, index) for index in range(64) ] for group in ['all', 'v=foo', 's=bar', 'l=somewhere'] }

In [46]:
presigs['all'][0]

(b'\x9f\n\x8e\xc9\x1d\xaf*\xac\x9e\x1as\xe8\xf8\xe6\xe9z',
 b'{\xd8\xb4\xaf\xb4PK1%*`\\\x8e\x93;\x82\xeaF\x99\xe0\xbfB\xf1\x9d\xae\x02|\xae\\?\x97\xb3\xa5j.Y\x83\xddg\x7f\x06\xd2\xa47^\xf3\xdd\x08n3\x90\x84~\x96,tO#\x8e$\xdc\xa2\x1a\r')

In [69]:
def validate_presig(group, index, key, presig, verify_key=sign_key.verify_key):
    """ Will raise an error for invalid signature or group/index """
    action_string = make_action_string(group, index)
    
    cipher = Cipher(algorithms.AES(key), modes.CTR(b'\0' * 16), backend=default_backend())
    dec = cipher.decryptor()
    plaintext = dec.update(presig)
    assert len(dec.finalize()) == 0
    
    return verify_key.verify(plaintext + action_string) == action_string

In [70]:
validate_presig('all', 0, *presigs['all'][0])

True